In [12]:
from transformers import AutoModelForCausalLM, AutoTokenizer

# 假设你已经加载了模型和tokenizer
model_path = "/home/mnt/wyx/src/Finetune-MiniCPM/finetune/output/cosmosqa/20240515212751/"
model = AutoModelForCausalLM.from_pretrained(model_path)
tokenizer = AutoTokenizer.from_pretrained(model_path)
res, history = model.chat(tokenizer, query="<用户>This is a reading comprehension task. Given the context: Good Old War and person L : I saw both of these bands Wednesday night , and they both blew me away . seriously . Good Old War is acoustic and makes me smile . I really can not help but be happy when I listen to them ; I think it 's the fact that they seemed so happy themselves when they played . Question: In the future , will this person go to see other bands play ? Which of the following is the correct answer related to the context? 0: None of the above choices . 1: This person likes music and likes to see the show , they will see other bands play . 2: This person only likes Good Old War and Person L , no other bands . 3: Other Bands is not on tour and this person can not see them.<AI>", max_length=384, top_p=0.5,eos_token_id=2, pad_token_id=2)
res, history

('1',
 [{'role': 'user',
   'content': "<用户>This is a reading comprehension task. Given the context: Good Old War and person L : I saw both of these bands Wednesday night , and they both blew me away . seriously . Good Old War is acoustic and makes me smile . I really can not help but be happy when I listen to them ; I think it 's the fact that they seemed so happy themselves when they played . Question: In the future , will this person go to see other bands play ? Which of the following is the correct answer related to the context? 0: None of the above choices . 1: This person likes music and likes to see the show , they will see other bands play . 2: This person only likes Good Old War and Person L , no other bands . 3: Other Bands is not on tour and this person can not see them.<AI>"},
  {'role': 'assistant', 'content': '1'}])

In [13]:
res, history = model.chat(tokenizer, query="<用户>This is a reading comprehension task. Given the context: I mean it : not one person said ANYTHING to me . They would have if I did something wrong , right ? But , this morning , I got a call from my guy at the temp agency and he said that I was no longer needed in that position , that I did n't need to go out there . Question: Why might have the temp agency tell me I am not needed at that position ? Which of the following is the correct answer related to the context? Please Only answer the question with a single number. 0: The company hiring the temp workers might have had a change of mind . 1: The temp agency hiring the temp workers might have had a change of mind . 2: None of the above choices . 3: I might have had a change of mind working for the company .<AI>", max_length=384, top_p=0.5,eos_token_id=2, pad_token_id=2)
res, history

('1',
 [{'role': 'user',
   'content': "<用户>This is a reading comprehension task. Given the context: I mean it : not one person said ANYTHING to me . They would have if I did something wrong , right ? But , this morning , I got a call from my guy at the temp agency and he said that I was no longer needed in that position , that I did n't need to go out there . Question: Why might have the temp agency tell me I am not needed at that position ? Which of the following is the correct answer related to the context? Please Only answer the question with a single number. 0: The company hiring the temp workers might have had a change of mind . 1: The temp agency hiring the temp workers might have had a change of mind . 2: None of the above choices . 3: I might have had a change of mind working for the company .<AI>"},
  {'role': 'assistant', 'content': '1'}])

<class 'str'>


In [8]:
import json

# 打开 JSON 文件
with open('/home/mnt/wyx/src/Finetune-MiniCPM/datasets/processed/cosmosqa/test.json', 'r', encoding='utf-8') as file:
    # 加载 JSON 数据
    data = json.load(file)




This is a reading comprehension task. Given the context: HGH and steroid use is rampant in track , and , just like in most American professional sports , any incredible individual achievement is questioned immediately , which is a sad state of affairs . The fact that we , as a human population have to assume that someone is using steroids because of an outstanding feat is horrible . What about the people who actually train their hearts out to achieve the same success that the users are trying to achieve ? It is n't fair to the men and women that dedicate their lives to achieving glory the right way , hard work and determination . Question: Why is HGH and steroid use rampant in track ? Which of the following is the correct answer related to the context? Please Only answer the question with a single number. 0: Because we have to assume that someone is using steroids because of an outstanding feat . 1: None of the above choices . 2: Because any incredible individual achievement is questio

In [4]:
import csv
from transformers import AutoModelForCausalLM, AutoTokenizer
import json
import torch
from tqdm import tqdm
import sys

# 检查CUDA是否可用，并设置设备
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)

# 加载模型和tokenizer，将模型移动到GPU
model_path = "/home/mnt/wyx/src/Finetune-MiniCPM/finetune/output/cosmosqa/20240515212751/"
model = AutoModelForCausalLM.from_pretrained(model_path).to(device)
tokenizer = AutoTokenizer.from_pretrained(model_path)

# 读取JSON文件
with open('/home/mnt/wyx/src/Finetune-MiniCPM/datasets/processed/cosmosqa/test.json', 'r', encoding='utf-8') as file:
    data = json.load(file)

def batch_inference(data, model, tokenizer, device, batch_size=4):
    results = []
    # tqdm包裹循环，提供进度条
    for i in tqdm(range(0, len(data), batch_size), desc="Processing batches"):
        batch = data[i:i+batch_size]
        inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=512)
        input_ids = inputs['input_ids'].to(device)
        attention_mask = inputs['attention_mask'].to(device)
        outputs = model.generate(input_ids, attention_mask=attention_mask, max_length=384, top_p=0.5, eos_token_id=2, pad_token_id=2)
        for output in outputs:
            result_text = tokenizer.decode(output, skip_special_tokens=True)
            print(result_text)
            sys.exit(1)
            results.append(result_text)
    return results

# 进行批量推理
results = batch_inference(data, model, tokenizer, device)

# 保存结果到CSV文件
with open('inference_results.csv', 'w', newline='', encoding='utf-8') as file:
    writer = csv.writer(file)
    writer.writerow(['question', 'model_answer'])
    for question, answer in zip(data, results):
        writer.writerow([question, answer])

print("Results have been saved to 'inference_results.csv'")


Using device: cuda


Processing batches:   0%|          | 0/1741 [00:00<?, ?it/s]


OutOfMemoryError: CUDA out of memory. Tried to allocate 20.00 MiB (GPU 0; 23.69 GiB total capacity; 21.65 GiB already allocated; 15.19 MiB free; 22.56 GiB reserved in total by PyTorch) If reserved memory is >> allocated memory try setting max_split_size_mb to avoid fragmentation.  See documentation for Memory Management and PYTORCH_CUDA_ALLOC_CONF

: 

In [2]:
print(results[0])

<用户>This is a reading comprehension task. Given the context: HGH and steroid use is rampant in track , and , just like in most American professional sports , any incredible individual achievement is questioned immediately , which is a sad state of affairs . The fact that we , as a human population have to assume that someone is using steroids because of an outstanding feat is horrible . What about the people who actually train their hearts out to achieve the same success that the users are trying to achieve ? It is n't fair to the men and women that dedicate their lives to achieving glory the right way , hard work and determination . Question: Why is HGH and steroid use rampant in track ? Which of the following is the correct answer related to the context? Please Only answer the question with a single number. 0: Because we have to assume that someone is using steroids because of an outstanding feat . 1: None of the above choices . 2: Because any incredible individual achievement is que

In [ ]:
import os
import json
import torch
import torch.distributed as dist
from torch.nn.parallel import DistributedDataParallel as DDP
from transformers import AutoModelForCausalLM, AutoTokenizer
from torch.utils.data import DataLoader, Dataset
from tqdm import tqdm

def setup(rank, world_size):
    os.environ['MASTER_ADDR'] = 'localhost'
    os.environ['MASTER_PORT'] = '12355'
    dist.init_process_group("nccl", rank=rank, world_size=world_size)
    torch.cuda.set_device(rank)

class TextDataset(Dataset):
    def __init__(self, texts):
        self.texts = texts

    def __len__(self):
        return len(self.texts)

    def __getitem__(self, idx):
        return self.texts[idx]

def cleanup():
    dist.destroy_process_group()

def batch_inference(rank, world_size, data):
    setup(rank, world_size)
    model_path = "/home/mnt/wyx/src/Finetune-MiniCPM/finetune/output/cosmosqa/20240515212751/"
    tokenizer = AutoTokenizer.from_pretrained(model_path)
    model = AutoModelForCausalLM.from_pretrained(model_path).to(rank)
    model = DDP(model, device_ids=[rank])

    dataset = TextDataset(data)
    sampler = torch.utils.data.distributed.DistributedSampler(dataset, num_replicas=world_size, rank=rank)
    dataloader = DataLoader(dataset, batch_size=10, sampler=sampler)

    model.eval()
    results = []
    with torch.no_grad():
        for batch in tqdm(dataloader, desc=f"Rank {rank} processing"):
            inputs = tokenizer(batch, return_tensors="pt", padding=True, truncation=True, max_length=512)
            input_ids = inputs['input_ids'].to(rank)
            attention_mask = inputs['attention_mask'].to(rank)
            outputs = model.generate(input_ids, attention_mask=attention_mask, max_length=384, top_p=0.5, eos_token_id=2, pad_token_id=2)
            for output in outputs:
                result_text = tokenizer.decode(output, skip_special_tokens=True)
                results.append(result_text)
    cleanup()
    return results

def main():
    world_size = 2  # 使用两个GPU
    data = json.load(open('/home/mnt/wyx/src/Finetune-MiniCPM/datasets/processed/cosmosqa/test.json', 'r', encoding='utf-8'))
    torch.multiprocessing.spawn(batch_inference,
                                args=(world_size, data),
                                nprocs=world_size,
                                join=True)

if __name__ == "__main__":
    main()
